## 5.3 データベースに対するアクセスの例 (1)

### 5.3.1 サンプルデータの作成

In [1]:
import sqlalchemy as SQLA   # SQLAlchemyを 'SQLA' の名で読込み
import pandas as pd         # pandasを 'pd' という名で読込み

In [2]:
df = pd.DataFrame( columns=['番号','氏名','英語','化学'] )  # DataFrameの作成
df['番号'] = [1,2,3]                              # '番号'のカラム
df['氏名'] = ['山田 太郎','田中 花子','中村 勝則']  # '氏名'のカラム
df['英語'] = [52,61,89]                           # '英語'のカラム
df['化学'] = [81,72,64]                           # '化学'のカラム
df      # 内容確認

番号     氏名  英語  化学
0   1  山田 太郎  52  81
1   2  田中 花子  61  72
2   3  中村 勝則  89  64

### 5.3.2 Engineオブジェクトの生成

In [3]:
egn = SQLA.create_engine( 'sqlite:///testdb01', echo=False )    # DB接続エンジンの生成

### 5.3.4 DataFrameのテーブルへの新規保存

In [4]:
df.to_sql( 'tbl01', egn, index=False )      # DataFrameをデータベースに保存

3

### 5.3.5 テーブルからDataFrameへの読込み

In [5]:
q = 'SELECT * FROM tbl01'       # SQLクエリ
df2 = pd.read_sql( q, egn )     # 読込みの実行
df2     # 内容確認

番号     氏名  英語  化学
0   1  山田 太郎  52  81
1   2  田中 花子  61  72
2   3  中村 勝則  89  64

### 5.3.6 既存のテーブルへの追加保存

In [6]:
df3 = pd.DataFrame( columns=['番号','氏名','英語','化学'] )  # DataFrameの作成
df3['番号'] = [4,5,6]                                 # '番号'のカラム
df3['氏名'] = ['吉田 たか子','ジョン スミス','リサ シェパード']   # '氏名'のカラム
df3['英語'] = [85,0,0]                              # '英語'のカラム
df3['化学'] = [52,0,0]                              # '化学'のカラム
df3     # 内容確認

番号        氏名  英語  化学
0   4    吉田 たか子  85  52
1   5   ジョン スミス   0   0
2   6  リサ シェパード   0   0

In [7]:
df3.to_sql( 'tbl01', egn, index=False, if_exists='append' ) # DataFrameをデータベースに追加

3

In [8]:
q = 'SELECT * FROM tbl01'       # SQLクエリ
df2 = pd.read_sql( q, egn )     # 読込みの実行
df2     # 内容確認

番号        氏名  英語  化学
0   1     山田 太郎  52  81
1   2     田中 花子  61  72
2   3     中村 勝則  89  64
3   4    吉田 たか子  85  52
4   5   ジョン スミス   0   0
5   6  リサ シェパード   0   0

### 5.3.7 既存のテーブルを新しいデータで置き換える

In [9]:
df3.to_sql( 'tbl01', egn, index=False, if_exists='replace' )      # テーブルの書き換え

3

In [10]:
q = 'SELECT * FROM tbl01'       # SQLクエリ
df2 = pd.read_sql( q, egn )     # 読込みの実行
df2     # 内容確認

番号        氏名  英語  化学
0   4    吉田 たか子  85  52
1   5   ジョン スミス   0   0
2   6  リサ シェパード   0   0

### 5.3.8 指定した条件によるデータの抽出

In [11]:
q = 'SELECT * FROM tbl01 WHERE 氏名="ジョン スミス" OR 氏名="リサ シェパード"'
df2 = pd.read_sql( q, egn )     # 読込みの実行
df2     # 内容確認

番号        氏名  英語  化学
0   5   ジョン スミス   0   0
1   6  リサ シェパード   0   0

## 5.4 データベースに対するアクセスの例 (2)

### 5.4.1 トランザクションの開始

In [12]:
cn = egn.connect()  # トランザクションの開始
print( type(cn) )   # データ型の調査

<class 'sqlalchemy.engine.base.Connection'>


### 5.4.2 既存のレコードの変更（データベースの更新）

In [13]:
r1 = cn.execute('UPDATE tbl01 SET 英語=99,化学=24  WHERE 氏名="ジョン スミス"')
r2 = cn.execute('UPDATE tbl01 SET 英語=100,化学=41 WHERE 氏名="リサ シェパード"')

In [14]:
q = 'SELECT * FROM tbl01'
df2 = pd.read_sql( q, egn )     # 読込みの実行
df2     # 内容確認

番号        氏名   英語  化学
0   4    吉田 たか子   85  52
1   5   ジョン スミス   99  24
2   6  リサ シェパード  100  41

### 5.4.3 既存のレコードの削除

In [15]:
r = cn.execute('DELETE FROM tbl01 WHERE 氏名="ジョン スミス"')

In [16]:
q = 'SELECT * FROM tbl01'
df2 = pd.read_sql( q, egn )     # 読込みの実行
df2     # 内容確認

番号        氏名   英語  化学
0   4    吉田 たか子   85  52
1   6  リサ シェパード  100  41

### 5.4.4.新規レコードの追加

In [17]:
r = cn.execute('''INSERT INTO tbl01 (番号, 氏名, 英語, 化学)
                    VALUES (5, "斉藤 ジェシカ", 93, 82)''')

In [18]:
q = 'SELECT * FROM tbl01'
df2 = pd.read_sql( q, egn )     # 読込みの実行
df2     # 内容確認

番号        氏名   英語  化学
0   4    吉田 たか子   85  52
1   6  リサ シェパード  100  41
2   5   斉藤 ジェシカ   93  82

### 5.4.5 executeメソッドの戻り値

In [19]:
r = cn.execute('SELECT * FROM tbl01')

In [20]:
print( r.keys() )
for rec in r:
    print( rec['番号'], rec['氏名'], rec['英語'],rec['化学'])

RMKeyView(['番号', '氏名', '英語', '化学'])
4 吉田 たか子 85 52
6 リサ シェパード 100 41
5 斉藤 ジェシカ 93 82


### 5.4.6 トランザクションの終了

In [21]:
cn.close()  # トランザクションの終了